In [110]:
import os
import sys, importlib
from dotenv import load_dotenv
import plotly.express as px
# Load Session Id vom .env file to environment variables
load_dotenv()

True

In [111]:
import pandas as pd

In [112]:
# Append the path to the exploratory-analysis package and import
sys.path.append(os.environ.get('PATH_EXPLORATORY_ANALYSIS'))
import exploratory_analysis as ea

In [113]:
data_path=os.environ.get('DATA_LOAN')

In [114]:
list_data=["credit_train.csv","credit_test.csv"]

_dfs=[pd.read_csv(os.path.join(data_path,_file_nm)) for _file_nm in list_data ]
df=pd.concat(_dfs)
# Delete rows all na
df.dropna(axis = 0, how = 'all', inplace = True)
df.head(5)

Loan ID                           Customer ID  \
0  14dd8831-6af5-400b-83ec-68e61888a048  981165ec-3274-42f5-a3b4-d104041a9ca9   
1  4771cc26-131a-45db-b5aa-537ea4ba5342  2de017a3-2e01-49cb-a581-08169e83be29   
2  4eed4e6a-aa2f-4c91-8651-ce984ee8fb26  5efb2b2b-bf11-4dfd-a572-3761a2694725   
3  77598f7b-32e7-4e3b-a6e5-06ba0d98fe8a  e777faab-98ae-45af-9a86-7ce5b33b1011   
4  d4062e70-befa-4995-8643-a0de73938182  81536ad9-5ccf-4eb8-befb-47a4d608658e   

  Loan Status  Current Loan Amount        Term  Credit Score  Annual Income  \
0  Fully Paid             445412.0  Short Term         709.0      1167493.0   
1  Fully Paid             262328.0  Short Term           NaN            NaN   
2  Fully Paid           99999999.0  Short Term         741.0      2231892.0   
3  Fully Paid             347666.0   Long Term         721.0       806949.0   
4  Fully Paid             176220.0  Short Term           NaN            NaN   

  Years in current job Home Ownership             Purpose  Monthly Debt  \
0              8 years  Home Mortgage   Home Improvements       5214.74   
1            10+ years  Home Mortgage  Debt Consolidation      33295.98   
2              8 years       Own Home  Debt Consolidation      29200.53   
3              3 years       Own Home  Debt Consolidation       8741.90   
4              5 years           Rent  Debt Consolidation      20639.70   

   Years of Credit History  Months since last delinquent  \
0                     17.2                           NaN   
1                     21.1                           8.0   
2                     14.9                          29.0   
3                     12.0                           NaN   
4                      6.1                           NaN   

   Number of Open Accounts  Number of Credit Problems  Current Credit Balance  \
0                      6.0                        1.0                228190.0   
1                     35.0                        0.0                229976.0   
2                     18.0                        1.0                297996.0   
3                      9.0                        0.0                256329.0   
4                     15.0                        0.0                253460.0   

   Maximum Open Credit  Bankruptcies  Tax Liens  
0             416746.0           1.0        0.0  
1             850784.0           0.0        0.0  
2             750090.0           0.0        0.0  
3             386958.0           0.0        0.0  
4             427174.0           0.0        0.0

In [115]:
basic_analysis_result=ea.basic_analysis_df(df)
df_basic_analysis=basic_analysis_result["df_info"]
num_cols=basic_analysis_result["num_cols"]
num_rows=basic_analysis_result["num_rows"]

In [116]:
print(f"Number Data: {num_rows}")

Number Data: 110000


In [117]:
# TODO: Add ratio to basic analysis function
df_basic_analysis["ratio_null"]=round(df_basic_analysis["num_null"]/num_rows,2)
df_basic_analysis

col_nm     type  num_unique  num_null  ratio_null
0                        Loan ID   object       88354         0        0.00
1                    Customer ID   object       88354         0        0.00
2                    Loan Status   object           2     10000        0.09
3            Current Loan Amount  float64       22502         0        0.00
4                           Term   object           2         0        0.00
5                   Credit Score  float64         326     21135        0.19
6                  Annual Income  float64       37853     21135        0.19
7           Years in current job   object          11      4649        0.04
8                 Home Ownership   object           4         0        0.00
9                        Purpose   object          16         0        0.00
10                  Monthly Debt  float64       69750         0        0.00
11       Years of Credit History  float64         507         0        0.00
12  Months since last delinquent  float64         116     58447        0.53
13       Number of Open Accounts  float64          52         0        0.00
14     Number of Credit Problems  float64          14         0        0.00
15        Current Credit Balance  float64       33641         0        0.00
16           Maximum Open Credit  float64       46468         2        0.00
17                  Bankruptcies  float64           8       226        0.00
18                     Tax Liens  float64          13        11        0.00

# How good is credit scoring for forecasting credit problem

In [118]:
_mask=df["Credit Score"].notna() & df["Loan Status"].notna()
df_credit_score=df[_mask].reset_index(drop=True)
df_credit_score=df_credit_score[["Credit Score","Loan Status"]]
df_credit_score["Credit Score"]=df_credit_score["Credit Score"].apply(int)
df_credit_score["len_digit_score"]=df_credit_score["Credit Score"].apply(lambda x: len(str(x)))
df_credit_score["Credit Score"]=[ _score if _len == 3 else int(str(_score)[:3]) for _score,_len in zip(df_credit_score["Credit Score"],df_credit_score["len_digit_score"])]
df_credit_score=df_credit_score.drop(columns = ["len_digit_score"])
df_credit_score.head(5)

Credit Score  Loan Status
0           709   Fully Paid
1           741   Fully Paid
2           721   Fully Paid
3           729  Charged Off
4           730   Fully Paid

In [119]:
fig = px.violin(df_credit_score, y="Credit Score", x="Loan Status", points="all", box=True)
fig.show()

--> Lower Credit Score tend to be charged off

--> Fully Paid credits is Multimodal with modes around 721 and 742

--> Charged-Off mode around 737

In [120]:
count_loan_status=df_credit_score.groupby("Loan Status",as_index=False)["Credit Score"].count().rename(columns={"Credit Score": "count"})
count_loan_status

Loan Status  count
0  Charged Off  17210
1   Fully Paid  63636

In [136]:
# Get Bins for Credit Score
df_credit_score["bin"]=pd.qcut(df_credit_score['Credit Score'], )

In [137]:
import numpy as np

In [157]:
def bin_iv(dataframe,col_to_bin,col_label,num_bin):
    dataframe["bin"]=pd.qcut(dataframe[col_to_bin], num_bin)
    count_bin_labeled=dataframe.groupby(["bin",col_label],as_index=False).count().rename(columns={col_to_bin:"count"})
    count_bin_labeled=count_bin_labeled.merge(count_loan_status.rename(columns={"count":"total"}),on=col_label, how="left")
    count_bin_labeled["ratio"]=count_bin_labeled["count"]/count_bin_labeled["total"]
    df_woe=pd.pivot_table(count_bin_labeled, values = 'ratio', index=['bin'], columns = 'Loan Status').reset_index()
    df_woe["woe"]=np.log(df_woe["Fully Paid"]/df_woe["Charged Off"])
    df_woe["iv"]=(df_woe["Fully Paid"]-df_woe["Charged Off"])*df_woe["woe"]
    return df_woe

In [158]:
_result=[]
for _bin in range(20):
    if _bin == 0:
        continue
    # df_credit_score["bin"]=pd.qcut(df_credit_score['Credit Score'], _bin)
    # count_bin_labeled=df_credit_score.groupby(["bin","Loan Status"],as_index=False).count().rename(columns={"Credit Score":"count"})
    # count_bin_labeled=count_bin_labeled.merge(count_loan_status.rename(columns={"count":"total"}),on="Loan Status", how="left")
    # count_bin_labeled["ratio"]=count_bin_labeled["count"]/count_bin_labeled["total"]
    # df_woe=pd.pivot_table(count_bin_labeled, values = 'ratio', index=['bin'], columns = 'Loan Status').reset_index()
    # df_woe["woe"]=np.log(df_woe["Fully Paid"]/df_woe["Charged Off"])
    # df_woe["iv"]=(df_woe["Fully Paid"]-df_woe["Charged Off"])*df_woe["woe"]
    df_woe=bin_iv(df_credit_score,"Credit Score","Loan Status",_bin)
    _result.append((_bin,df_woe["iv"].sum()))

_arg_max=np.argmax([_res[1] for _res in _result])
opt_bin=_result[_arg_max][0]
print(f"Optimal number of bin: {opt_bin}")

Optimal number of bin: 16


In [185]:
df_woe

Loan Status               bin  Charged Off  Fully Paid       woe        iv
0            (584.999, 665.0]     0.100116    0.053790 -0.621238  0.028779
1              (665.0, 684.0]     0.086752    0.059510 -0.376902  0.010267
2              (684.0, 695.0]     0.069494    0.057892 -0.182672  0.002119
3              (695.0, 703.0]     0.067635    0.063298 -0.066281  0.000288
4              (703.0, 709.0]     0.064033    0.063030 -0.015775  0.000016
5              (709.0, 714.0]     0.056653    0.062968  0.105672  0.000667
6              (714.0, 718.0]     0.053167    0.061899  0.152069  0.001328
7              (718.0, 722.0]     0.058164    0.069646  0.180163  0.002069
8              (722.0, 725.0]     0.044102    0.062135  0.342792  0.006181
9              (725.0, 731.0]     0.097037    0.066943 -0.371243  0.011172
10             (731.0, 735.0]     0.072865    0.055283 -0.276135  0.004855
11             (735.0, 738.0]     0.058396    0.052407 -0.108204  0.000648
12             (738.0, 741.0]     0.061069    0.068248  0.111135  0.000798
13             (741.0, 744.0]     0.047937    0.065215  0.307791  0.005318
14             (744.0, 747.0]     0.041371    0.073056  0.568641  0.018017
15             (747.0, 751.0]     0.021209    0.064680  1.115051  0.048473

In [187]:
df_woe=bin_iv(df_credit_score,"Credit Score","Loan Status",10)
df_woe

Loan Status               bin  Charged Off  Fully Paid       woe        iv
0            (584.999, 678.0]     0.154387    0.089918 -0.540568  0.034850
1              (678.0, 697.0]     0.116967    0.094585 -0.212394  0.004754
2              (697.0, 708.0]     0.105055    0.101656 -0.032888  0.000112
3              (708.0, 716.0]     0.093434    0.102788  0.095410  0.000892
4              (716.0, 722.0]     0.086171    0.103086  0.179235  0.003032
5              (722.0, 729.0]     0.108774    0.104202 -0.042940  0.000196
6              (729.0, 736.0]     0.122080    0.095103 -0.249713  0.006736
7              (736.0, 741.0]     0.102615    0.105711  0.029723  0.000092
8              (741.0, 746.0]     0.076990    0.112122  0.375911  0.013206
9              (746.0, 751.0]     0.033527    0.090829  0.996628  0.057109

In [163]:
df_woe=bin_iv(df_credit_score,"Credit Score","Loan Status",opt_bin)
bins_woe=list(df_woe["bin"].unique())
bins_woe

[Interval(584.999, 665.0, closed='right'),
 Interval(665.0, 684.0, closed='right'),
 Interval(684.0, 695.0, closed='right'),
 Interval(695.0, 703.0, closed='right'),
 Interval(703.0, 709.0, closed='right'),
 Interval(709.0, 714.0, closed='right'),
 Interval(714.0, 718.0, closed='right'),
 Interval(718.0, 722.0, closed='right'),
 Interval(722.0, 725.0, closed='right'),
 Interval(725.0, 731.0, closed='right'),
 Interval(731.0, 735.0, closed='right'),
 Interval(735.0, 738.0, closed='right'),
 Interval(738.0, 741.0, closed='right'),
 Interval(741.0, 744.0, closed='right'),
 Interval(744.0, 747.0, closed='right'),
 Interval(747.0, 751.0, closed='right')]

In [169]:
def assign_bin(value,bins):
    for _bin in bins:
        if value in _bin:
            return str(_bin)

In [171]:
df_credit_score["bin"]=df_credit_score["Credit Score"].apply(lambda x: assign_bin(x,bins_woe))

In [184]:
fig = px.violin(df_credit_score, y="Credit Score", x="bin",color="Loan Status", points="all", box=True)
fig.update_xaxes(categoryorder='array', categoryarray=[str(_int) for _int in list(df_woe["bin"].unique().categories)])
fig.show()

In [172]:
df_credit_score

Credit Score  Loan Status             bin
0               709   Fully Paid  (703.0, 709.0]
1               741   Fully Paid  (738.0, 741.0]
2               721   Fully Paid  (718.0, 722.0]
3               729  Charged Off  (725.0, 731.0]
4               730   Fully Paid  (725.0, 731.0]
...             ...          ...             ...
80841           725   Fully Paid  (722.0, 725.0]
80842           732   Fully Paid  (731.0, 735.0]
80843           742   Fully Paid  (741.0, 744.0]
80844           746   Fully Paid  (744.0, 747.0]
80845           743   Fully Paid  (741.0, 744.0]

[80846 rows x 3 columns]

In [ ]:
fig = px.violin(df_credit_score, y="Credit Score", x="Loan Status", points="all", box=True)
fig.show()

In [153]:
_arg_max=np.argmax([_res[1] for _res in _result])
opt_bin=_result[_arg_max][0]
opt_bin

16

In [140]:
# Weight of evidence
count_bin_labeled=df_credit_score.groupby(["bin","Loan Status"],as_index=False).count().rename(columns={"Credit Score":"count"})
count_bin_labeled=count_bin_labeled.merge(count_loan_status.rename(columns={"count":"total"}),on="Loan Status", how="left")
count_bin_labeled["ratio"]=count_bin_labeled["count"]/count_bin_labeled["total"]
df_woe=pd.pivot_table(count_bin_labeled, values = 'ratio', index=['bin'], columns = 'Loan Status').reset_index()
df_woe["woe"]=np.log(df_woe["Charged Off"]/df_woe["Fully Paid"])
df_woe["iv"]=(df_woe["Charged Off"]-df_woe["Fully Paid"])*df_woe["woe"]
df_woe["iv"].sum()

0.12098006472216646

In [139]:
df_woe["iv"].sum()

0.12098006472216645

In [109]:
count_bin_labeled[count_bin_labeled["Loan Status"] == "Charged Off"]

bin  Loan Status  count  total     ratio
0   (584.834, 601.6]  Charged Off     87  17210  0.005055
2     (601.6, 618.2]  Charged Off    170  17210  0.009878
4     (618.2, 634.8]  Charged Off    288  17210  0.016734
6     (634.8, 651.4]  Charged Off    477  17210  0.027716
8     (651.4, 668.0]  Charged Off    892  17210  0.051830
10    (668.0, 684.6]  Charged Off   1302  17210  0.075654
12    (684.6, 701.2]  Charged Off   2055  17210  0.119407
14    (701.2, 717.8]  Charged Off   3054  17210  0.177455
16    (717.8, 734.4]  Charged Off   4612  17210  0.267984
18    (734.4, 751.0]  Charged Off   4273  17210  0.248286

In [94]:
#function to calculate Weight of Evidence (WoE) and Information Value (IV)

def iv_woe(data, target, bins=10, show_woe=False):
    
    newDF,woeDF = pd.DataFrame(), pd.DataFrame()
    cols = data.columns
    
    #Run WoE and IV on all the independent variables
    for ivars in cols[~cols.isin([target])]:
        if (data[ivars].dtype.kind in 'bifc') and (len(np.unique(data[ivars]))>10):
            binned_x = pd.qcut(data[ivars], bins,  duplicates='drop')
            d0 = pd.DataFrame({'x': binned_x, 'y': data[target]})
        else:
            d0 = pd.DataFrame({'x': data[ivars], 'y': data[target]})
        d = d0.groupby("x", as_index=False).agg({"y": ["count", "sum"]})
        d.columns = ['Cutoff', 'N', 'Events']
        d['% of Events'] = np.maximum(d['Events'], 0.5) / d['Events'].sum()
        d['Non-Events'] = d['N'] - d['Events']
        d['% of Non-Events'] = np.maximum(d['Non-Events'], 0.5) / d['Non-Events'].sum()
        d['WoE'] = np.log(d['% of Events']/d['% of Non-Events'])
        d['IV'] = d['WoE'] * (d['% of Events'] - d['% of Non-Events'])
        d.insert(loc=0, column='Variable', value=ivars)
        print("Information value of " + ivars + " is " + str(round(d['IV'].sum(),6)))
        temp =pd.DataFrame({"Variable" : [ivars], "IV" : [d['IV'].sum()]}, columns = ["Variable", "IV"])
        newDF=pd.concat([newDF,temp], axis=0)
        woeDF=pd.concat([woeDF,d], axis=0)

        if show_woe == True:
            print(d)
            
    return newDF, woeDF

iv, woe = iv_woe(, target='bad_loan', bins=20)

In [95]:
BinGenerator(df_credit_score,"Credit Score","Loan Status")._generate_correct_bins()

/Users/ezratampubolon/PythonProjects/exploratory-analysis/.venv/lib/python3.10/site-packages/scipy/stats/_stats_py.py:112: RuntimeWarning:

The input array could not be properly checked for nan values. nan values will be ignored.

/Users/ezratampubolon/PythonProjects/exploratory-analysis/.venv/lib/python3.10/site-packages/scipy/stats/_stats_py.py:112: RuntimeWarning:

The input array could not be properly checked for nan values. nan values will be ignored.

/Users/ezratampubolon/PythonProjects/exploratory-analysis/.venv/lib/python3.10/site-packages/scipy/stats/_stats_py.py:112: RuntimeWarning:

The input array could not be properly checked for nan values. nan values will be ignored.

/Users/ezratampubolon/PythonProjects/exploratory-analysis/.venv/lib/python3.10/site-packages/scipy/stats/_stats_py.py:112: RuntimeWarning:

The input array could not be properly checked for nan values. nan values will be ignored.

/Users/ezratampubolon/PythonProjects/exploratory-analysis/.venv/lib/python3.

bin  Credit Score                                        Loan Status
0  584         40880  Fully PaidFully PaidFully PaidCharged OffCharg...
1  722         39966  Fully PaidCharged OffFully PaidFully PaidFully...

In [72]:
_generate_bins(df_credit_score,"Credit Score","Loan Status",5,int)

Credit Score  Loan Status  bin
0               709   Fully Paid  697
1               741   Fully Paid  729
2               721   Fully Paid  716
3               729  Charged Off  716
4               730   Fully Paid  729
...             ...          ...  ...
80841           725   Fully Paid  716
80842           732   Fully Paid  729
80843           742   Fully Paid  741
80844           746   Fully Paid  741
80845           743   Fully Paid  741

[80846 rows x 3 columns]